
# Plot electrical conductivity vs. temperature for a plasma of methane.

The electrical conductivity of a plasma is the ability of the plasma to conduct an electric current.
It is a key parameter in the study of plasmas, as it determines the behavior of the plasma in the presence
of an electric field.

It assumed that the plasma is in local thermodynamic equilibrium (LTE), which means that all temperatures
are equal.


## Equilibrium composition
The following species are considered in the mechanism:

- H, H2, C, CH, CH2, CH3, CH4, C2, C2H, C2H2, C2H3, C2H4, C2H5, C2H6,
- corresponding ions,
- electrons,
- no solid carbon species.

Data comes from the following sources:

- [GRCDatabase]_ for neutral species, C+, C2+, CH+, H+ and H2+, and for electrons,
- [Burcat]_ for the other ions.

The thermo data are given as NASA 9 polynomial coefficients (For details, see
https://cantera.org/stable/reference/thermo/species-thermo.html#the-nasa-9-coefficient-polynomial-parameterization).

The temperature range is from 200 to 20000 K for atomic species, and from 200 to 6000 K for molecular species.

Then, to compute the equilibrium composition of the plasma, the Gibbs free energy minimization method is used.


## Electrical conductivity computation
The computation presented here is based on [Raizer1991]_.:

The weakly ionized electrical conductivity is given by the following formula:

\begin{align}\sigma_{\text{weakly ionized}} = \frac{n_e e^2}{m_e \nu_{en}}\end{align}

where:

- $\sigma_{\text{weakly ionized}}$ is the weakly ionized electrical conductivity,
- $n_e$ is the electron number density,
- $e$ is the elementary charge,
- $\nu_{en}$ is the electron-neutral collision frequency,
- $m_e$ is the electron mass.

The electron-neutral collision frequency is given by the following formula:

\begin{align}\nu_{en} = n_h \sigma_{\text{elastic}} v_e\end{align}

where:

- $n_h$ is the neutral number density,
- $\sigma_{\text{elastic}}$ is the elastic collision cross-section,
- $v_e$ is the electron thermal velocity.

The strongly ionized electrical conductivity is given by the Spitzer formula:

\begin{align}\sigma_{\text{strongly ionized}} = \text{Spitzer constant} \times \frac{T_e^{3/2}}{\log(\lambda)}\end{align}

where:

- $\sigma_{\text{strongly ionized}}$ is the strongly ionized electrical conductivity,
- $T_e$ is the electron temperature,
- $\text{Spitzer constant}$ is a constant that depends on the physical constants,
- $\log(\lambda)$ is the Coulomb logarithm.


Since frequencies can be added up, the total electrical conductivity is given by:

\begin{align}\sigma_{\text{total}} = \frac{1}{
                        \frac{1}{\sigma_{\text{weakly ionized}}} + \frac{1}{\sigma_{\text{strongly ionized}}}
                    }\end{align}


Comparisons are made for the various models of elastic cross-sections:

- Hard sphere model: The mean cross section is computed assuming that species are hard spheres.
- Tabulated model CH4: The mean cross section is computed using tabulated data of cross sections vs. energy
  for methane.
- Tabulated model all: The mean cross section is computed using tabulated data of cross sections vs. energy
    for all available species.

The differents electrical conductivities resulting from these models are compared to the data of FCP.


## Import the required libraries.



In [ ]:
import cantera as ct
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

from rizer.io.thermo_transport_data_reader import ThermoTransportDataReader
from rizer.misc.units import Units
from rizer.misc.utils import get_path_to_data
from rizer.plasma.collision_frequency import (
    MomentumTransferCollisionFrequencyModel,
    get_momentum_transfer_collision_frequency_model,
)
from rizer.plasma.momentum_transfer_cross_sections import (
    HardSphereCrossSection,
    MomentumTransferCrossSectionModel,
    get_momentum_transfer_cross_section_model,
)

sns.set_theme("poster")
u = Units()

## Define the thermo data files to load.



In [ ]:
mechanism = get_path_to_data("mechanisms", "Goutier2025", "CH4_to_C2H2.yaml")

# Load the gas phase.
gas = ct.Solution(
    mechanism,
    name="gas",
    transport_model=None,
)

## Define the temperature range and the pressure.



In [ ]:
temperatures = np.linspace(300, 30000, 1000, dtype=float)  # K
pressure = ct.one_atm  # Pa

## Create the models for the elastic cross sections.



In [ ]:
# Hard sphere model.
effective_radius = 1e-10  # m
model_1 = HardSphereCrossSection(effective_radius)
effective_radius = 3.5e-10  # m
model_2 = HardSphereCrossSection(effective_radius)

# Tabulated model, based on CH4 data.
model_3 = get_momentum_transfer_cross_section_model(
    species="CH4",
    database_to_use="Morgan.txt",
)

# Tabulated model, based on all available data.
species_list = [
    "H",
    "H2",
    "C",
    "CH4",
    "C2H2",
    "C2H4",
    "C2H6",
    "H+",
    "H2+",
    "C+",
    "CH4+",
    "C2H2+",
    "C2H4+",
    "C2H6+",
]

model_4 = [
    get_momentum_transfer_collision_frequency_model(
        species=species,
        use_default_radius=False,
        use_first_available=True,
    )
    for species in species_list
]

models: list[MomentumTransferCrossSectionModel] = [
    model_1,
    model_2,
    model_3,
]

## Compute the electrical conductivity.



In [ ]:
electrical_conductivities = np.zeros((len(temperatures), len(models) + 1))

for i, T in enumerate(temperatures):
    # Set the temperature and composition.
    gas.TPX = T, pressure, "CH4:1"

    # Equilibrate the gas.
    gas.equilibrate("TP")

    # Get the mole fractions of the electrons and the neutral species.
    x_e = gas.mole_fraction_dict()["e-"]

    # Get the total number density and the number densities of the electrons and the neutral species.
    n_tot = pressure / (u.k_b * T)  # m^-3
    n_e = x_e * n_tot  # m^-3

    # Get the number density of the neutral species (CH4).
    # It assumed to be the main species in the plasma.
    n_CH4 = (1 - x_e) * n_tot  # m^-3

    for j, model in enumerate(models):
        nu_model = MomentumTransferCollisionFrequencyModel(
            name=model.name,
            cross_section_model=model,
        )

        # Get the electron thermal velocity.
        nu = nu_model.get_mean_momentum_transfer_collision_frequency(T, n_CH4, n_e=n_e)

        # Compute the total electrical conductivity.
        σ_total = u.e**2 * n_e / (u.m_e * nu)  # S/m

        electrical_conductivities[i, j] = σ_total

    # For the last model, use a more complete model.
    nu_tot = 0.0
    nu_tot_ions = 0.0
    for k, species in enumerate(species_list):
        x_k = gas.mole_fraction_dict()[species]
        n_k = x_k * n_tot  # m^-3
        # print(f"Species: {species}, Mole fraction: {x_k:.4e}, Density: {n_k:.4e} m^-3"       )
        # print(type())
        nu = model_4[k].get_mean_momentum_transfer_collision_frequency(
            T, n_h=n_k, n_e=n_e
        )
        nu_tot += nu
        if species in ["H+", "H2+", "C+", "CH4+", "C2H2+", "C2H4+", "C2H6+"]:
            nu_tot_ions += nu

    # Compute the total electrical conductivity.
    σ_total = u.e**2 * n_e / (u.m_e * nu_tot)  # S/m

    # If the number density of ions is greater than the number density of neutrals,
    # we can assume that the plasma is strongly ionized.
    nu_tot_neutrals = nu_tot - nu_tot_ions
    if nu_tot_ions > 10 * nu_tot_neutrals:
        σ_total *= 1.98  # Spitzer constant for strongly ionized plasma, see (II 13.18) of [Mitchner1973]_.

    electrical_conductivities[i, len(models)] = σ_total

## Load reference data.



In [ ]:
data_CH4_Wu2016_Niu2016 = ThermoTransportDataReader(
    gas_name="CH4",
    pressure_atm=1,
    source="Wu2016_Niu2016",
    skip_missing_values=True,
)

## Plot the electrical conductivity vs. temperature.



In [ ]:
fig, ax = plt.subplots(figsize=(12, 8), layout="constrained")

for j, model in enumerate(models):
    ax.plot(temperatures, electrical_conductivities[:, j], label=model.name)

ax.plot(
    temperatures,
    electrical_conductivities[:, len(models)],
    label="All species",
    color="black",
    linewidth=2,
)

ax.plot(
    data_CH4_Wu2016_Niu2016.temperature,
    data_CH4_Wu2016_Niu2016.electrical_conductivity,
    "--",
    label="FCP",
)
ax.set_xlabel("Temperature [K]")
ax.set_ylabel("Electrical conductivity [S/m]")
ax.set_title("Electrical conductivity of a plasma of methane")
ax.legend()
ax.set_yscale("log")
ax.set_ylim(1e-2, 1e6)


plt.show()